In [1]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split

import dataset
import test_lstm

2023-03-12 01:53:36.396452: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [42]:
#Models - LSTM and Transformer

class positionalEncoder(nn.Module):

  def __init__(self, frame_length, encoding_length):
    super().__init__()

    embedding = nn.Embedding(frame_length, encoding_length)

    self.pe = embedding(torch.tensor([i for i in range(frame_length)]).unsqueeze(1)).squeeze()

  def forward(self, x):

    embedded = []

    if len(x.shape) == 3:
      for i in range(x.shape[0]):
        embedded.append(torch.cat((x[i], self.pe), 1).detach().numpy())
      return torch.tensor(embedded)
    else:
      return torch.cat((x, self.pe), 1)

class classifierTransformer(nn.Module):

  def __init__(self, inFeatCount, num_T_layers, num_frames, device, pos_encode_size = 5, n_heads = 4, n_hidden = 2048, dropout = 0.3, outFeatCount = 2):
    super().__init__()

    self.posEncoder = positionalEncoder(num_frames, pos_encode_size)

    heads = n_heads
    num_features = inFeatCount + pos_encode_size

    if (num_features % heads) != 0:
      heads += heads - (num_features % heads)

    print(f'features = {num_features}, heads = {heads}')

    n_hidden = max(n_hidden, 2*num_features)

    encoder_layer = nn.TransformerEncoderLayer(inFeatCount + pos_encode_size, heads, n_hidden, dropout)
    self.encoder = nn.TransformerEncoder(encoder_layer, num_T_layers)
    
    many_to_one_feat = num_frames * num_features
    mid = (many_to_one_feat - outFeatCount) // 2 + outFeatCount

    self.fc1 = nn.Linear(many_to_one_feat, mid)
    self.fc2 = nn.Linear(mid, 2)

    self.device = device

    self.init_weights()

  def init_weights(self):
      initrange = 0.1
      self.fc1.bias.data.zero_()
      self.fc1.weight.data.uniform_(-initrange, initrange)

      self.fc2.bias.data.zero_()
      self.fc2.weight.data.uniform_(-initrange, initrange)

  def forward(self, x):
    
    #x.shape = [num_frames, feat_count]
    encoded = self.posEncoder(x)

    #encoded.shape = [num_frames, feat_count + pos_encoding_count]
    data = self.encoder(encoded)

    #data.shape = [num_frames, feat_count + pos_encoding_count]
    if len(data.shape) == 3:
      data = torch.reshape(data, (data.shape[0], data.shape[1] * data.shape[2]))
    else:
      data = torch.reshape(data, (1,-1))

    #data.shape = [1, num_frames * (feat_count + pos_encoding_count)] 

    data = self.fc1(data)
    data = self.fc2(data)
    ##data = nn.functional.softmax(data, dim = 1).to(self.device) 

    return torch.tensor(data.tolist()).float()

class classifierLSTM(nn.Module):
  
  def __init__(self, input_size, hidden_size, frame_count, device, dropout = 0.3, output_size = 2):

    super().__init__()
    
    self.lstm = nn.LSTM(input_size, hidden_size, batch_first=True)
    self.dropout = nn.Dropout(dropout)
    self.fc = nn.Linear((hidden_size * frame_count), output_size)
    self.device = device

  def forward(self, x):
    x = x.unsqueeze(0)
    pred, _ = self.lstm(x)
    dropped = self.dropout(pred[-1])

    data = torch.reshape(dropped, (1,-1))
    #reshape to [1, num_frames * hidden_size]

    data = self.fc(data)
    data = nn.functional.softmax(data, dim = 1).to(self.device)

    return data.tolist()[0]

In [3]:
#data prep

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

lie_trial_path = './processed_lie/' #60 entries
truth_trial_path = './processed_truth/' #61 entries
MU3D_path = './processed/' # 300 entries

# no split by person
numOfFrames = 10

X, Y = dataset.preprocessing(truth_trial_path, lie_trial_path, numOfFrames=numOfFrames)

TEST_RATIO = 0.2

xTrain, xTest = train_test_split(X, test_size=TEST_RATIO, shuffle=False)
yTrain, yTest = train_test_split(Y, test_size=TEST_RATIO, shuffle=False)

yTrain_temp, yTest_temp = [], []

for i in range(yTrain.shape[0]):
    yTrain_temp.append([1,0]) if yTrain[i] == 0 else yTrain_temp.append([0,1])

for i in range(yTest.shape[0]):
    yTest_temp.append([1,0]) if yTest[i] == 0 else yTest_temp.append([0,1])

y_Train = torch.tensor(yTrain_temp).to(device)
y_Test = torch.tensor(yTest_temp).to(device)

x_Train = torch.tensor(xTrain, dtype=torch.float32).to(device)
x_Test = torch.tensor(xTest, dtype=torch.float32).to(device)

In [56]:
#model prep
featCount = 10
num_frames = 10
encoder_layers = 2
LSTM_hidden = 256

Transformer = classifierTransformer(featCount, encoder_layers, num_frames, device)
LSTM = classifierLSTM(featCount, LSTM_hidden, num_frames, device)

# training
def train(model, xTrain, yTrain, xTest, yTest, epochs = 100, lr = 0.05, batch_size = 10):
    """ Train a model on a dataset """
    
    # create a data loader to handle batching
    xTrain_loader =  torch.utils.data.DataLoader(xTrain, batch_size=batch_size, shuffle=False)
    xTest_loader = torch.utils.data.DataLoader(xTest, batch_size=batch_size, shuffle=False)

    # create a loss function and optimizer
    loss_fn = nn.CrossEntropyLoss()
    optimizer = torch.optim.Adam(model.parameters(), lr=lr)

    # train the model
    for epoch in range(epochs):

        # train

        idx = 0
        model.train()

        tot_loss = 0
        for batch in xTrain_loader:

            # get data
            x_train = torch.tensor(batch, requires_grad=True).to(device).float()
            y_train = torch.tensor(yTrain[idx:min(idx+batch_size,len(yTrain))]).float().to(device)
            
            optimizer.zero_grad()

            # forward pass
            y_pred = model(x_train)

            print("actual for batch ", idx, " is ", torch.argmax(y_train, dim=1).long())
            print("my prediction for batch ", idx, " is ", torch.argmax(y_pred, dim=1).long())

            # compute loss
            loss = loss_fn(y_pred,torch.argmax(y_train, dim=1).long())
            loss.requires_grad = True

            print("raw prediction for batch ", idx, " is ", y_pred)
            print("loss for batch ", idx, " is ", loss.item())

            tot_loss += loss.item()
            
            # backward pass
            loss.backward()

            # update weights
            optimizer.step()

            #idx += batch_size

        print(f'Epoch {epoch+1}/{epochs}, Loss: {tot_loss:.4f}')

        # evaluate
        model.eval()

        # test_acc = 0
        # acc = 0
        # tot_loss = 0

        # with torch.no_grad():
            
        #     idx_test = 0
        #     for batch in xTest_loader:
        #         xTest = batch.to(device).float()
        #         y_pred = model(xTest)

        #         # compute test accuracy
        #         # test_acc += (y_pred == y_test).float().mean().item()
        #         # idx_test += batch_size

        #         if idx_test == 0:
        #             print(model(xTest))
                

        #     test_acc /= len(xTest)  
        #     test_accuracy_items.append(test_acc)

        #     idx_train = 0
        #     for batch in xTrain_loader:
        #         xTrain = batch.to(device).float()
        #         y_pred = model(xTrain)
        #         y_train = torch.tensor(yTrain[idx_train:min(idx_train+batch_size,len(yTrain))]).to(device).float()

        #         # compute accuracy
        #         # acc += (y_pred == y_train).float().mean().item()
        #         # idx_train += 1

        #         # computer loss
        #         tot_loss += loss_fn(y_pred, y_train).item()
        #         idx_train += batch_size

        #     acc /= len(xTrain)
        #     accuracy_items.append(acc)

        # # store loss and accuracy
        # loss_items.append(tot_loss)

        # print progress
        
        

        idx += 1
            

train(Transformer, xTrain, y_Train, xTest, y_Test)

features = 15, heads = 5
actual for batch  0  is  tensor([1, 1, 1, 1, 0, 0, 1, 0, 0, 1])
my prediction for batch  0  is  tensor([1, 1, 1, 1, 1, 0, 1, 1, 1, 1])
raw prediction for batch  0  is  tensor([[ 0.1132,  0.6206],
        [-0.1359,  0.5681],
        [ 0.0493,  0.4576],
        [-0.0007,  0.3742],
        [ 0.3577,  0.4977],
        [ 0.3034,  0.1753],
        [ 0.1485,  0.6626],
        [ 0.0774,  0.3440],
        [ 0.2611,  0.4131],
        [-0.0583,  0.3589]])
loss for batch  0  is  0.5885072946548462
actual for batch  0  is  tensor([1, 1, 1, 1, 0, 0, 1, 0, 0, 1])
my prediction for batch  0  is  tensor([0, 0, 1, 1, 1, 1, 1, 1, 1, 1])
raw prediction for batch  0  is  tensor([[ 0.1343,  0.0919],
        [-0.0415, -0.0662],
        [-0.0882,  0.3700],
        [-0.0470,  0.4822],
        [-0.3193,  0.7176],
        [ 0.0581,  0.6292],
        [-0.2261,  0.5365],
        [-0.1227,  0.3823],
        [-0.1315,  0.4156],
        [ 0.0989,  0.3135]])
loss for batch  0  is  0.7687891721

/var/folders/66/pn8653k51_75x5ksbpsy8hm80000gn/T/ipykernel_28069/3805204262.py:34: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_train = torch.tensor(batch, requires_grad=True).to(device).float()
/var/folders/66/pn8653k51_75x5ksbpsy8hm80000gn/T/ipykernel_28069/3805204262.py:35: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_train = torch.tensor(yTrain[idx:min(idx+batch_size,len(yTrain))]).float().to(device)


actual for batch  0  is  tensor([1, 1, 1, 1, 0, 0, 1, 0, 0, 1])
my prediction for batch  0  is  tensor([1, 1, 1, 1, 1, 1, 1, 1, 1, 1])
raw prediction for batch  0  is  tensor([[-0.0490,  0.2910],
        [-0.4278,  0.3669],
        [-0.0983,  0.4214],
        [ 0.1752,  0.4530],
        [-0.2511,  0.5823],
        [-0.1356,  0.6980],
        [ 0.0293,  0.5960],
        [-0.1211,  0.3318],
        [-0.3939,  0.4633],
        [ 0.2369,  0.4629]])
loss for batch  0  is  0.7521321773529053
actual for batch  0  is  tensor([1, 1, 1, 1, 0, 0, 1, 0, 0, 1])
my prediction for batch  0  is  tensor([1, 1, 1, 1, 1, 1, 1, 1, 1, 1])
raw prediction for batch  0  is  tensor([[-0.2557,  0.5803],
        [-0.0486,  0.4811],
        [-0.2745,  0.6709],
        [-0.0420,  0.4701],
        [-0.0540,  0.2944],
        [-0.2265,  0.4697],
        [ 0.0977,  0.5244],
        [ 0.0250,  0.3811],
        [-0.2481,  0.2854],
        [ 0.0259,  0.5689]])
loss for batch  0  is  0.6446463465690613
actual for batch  

KeyboardInterrupt: 